# Coursera IBM Data Science Professional Capstone Project

# Auto-workshop location for a new business in Hamilton, Ontario
 ## Report written by Abiola D. Obembe
   ### Date: 23-01-2020

# 1.	Introduction

# 1.1 Background


Hamilton is a port city in the Canadian province of Ontario. An industrialized city in the Golden Horseshoe at the west end of Lake Ontario, Hamilton has a population of 536,917, and its census metropolitan area, which includes Burlington and Grimsby, has a population of 747,545. The city is 58 kilometres (36 mi) southwest of Toronto, with which the Greater Toronto and Hamilton Area (GTHA) is formed. On January 1, 2001, the current boundaries of Hamilton were created through the amalgamation of the original city with other municipalities of the Regional Municipality of Hamilton–Wentworth. Residents of the city are known as Hamiltonians. Since 1981, the metropolitan area has been listed as the ninth largest in Canada and the third largest in Ontario. Hamilton is home to the Royal Botanical Gardens, the Canadian Warplane Heritage Museum, the Bruce Trail, McMaster University, Redeemer University College and Mohawk College. McMaster University is ranked 4th in Canada and 77th in the world by Times Higher Education Rankings 2018–19.

# 1.2 Problem statement
Mr. Jenkins has recently migrated to Ontario, Canada as a permanent resident and currently lives in the city of Hamilton. His long-term goal is to be an entrepreneur and hence part of the reasons he decided to relocate with his family to Canada. Apart from having huge funds to invest in a profitable business, the Canadian government offers incentives and tax waivers to business owners to assist entrepreneurs to establish an auto businesses in Canada. After spending a few months in the city of Hamilton, Mr. Jenkins is excited to start his business in the city. However, after a careful study of the city, he is confident establishing an automobile repair workshop will be profitable. However, he is unsure of the best location for the workshop. The aim of this project is to utilize available data from the city of Hamilton and Foursquare location data to advise Mr. Jenkins on potential location(s) for his workshop. 


# 2. Data Section

The data to be employed for this project will be obtained from the city of Hamilton website from the following webpage http://open.hamilton.ca/datasets/ac6fc684043341f6b1d6298c146a0bcf_1. Specifically, the webpage has data on the distinct municipal addresses in Hamilton. This dataset exists as both CSV files and GEOJSON files. Besides, the original dataset consists of 253,876 rows of data and 13 columns (features). Observation of the CSV dataset reveals that the features include: "X-Coordinate", "Y-Coordinate"," Object ID", "Longitude", "Latitude",  "Number Complete",  "Unit Number Complete", " Full Street Name", "Settlement",  "Community", "Muncipality", "Country", "Province.

Further inspection of the dataset indicates that the community in the city of Hamilton is divided into six which include; Hamilton, Dundas, Stoney Creek, Ancaster, Flamborough, and Glanbrook. Furthermore, the columns labeled  "X-Coordinate", "Y-Coordinate"," Object ID",  "Number Complete",  "Unit Number Complete",  "Settlement",  "Muncipality", "Country", and  "Province do not add additional information and would be neglected from this analysis. In addition, for convenience and to reduce compuational time, only the 100000 rows of data will be employed for analysis.

Finally,  Foursquare data will be employed to explore venues in the city of Hamilton (i.e. community of Hamilton) to have a proper understanding of trending venues and the best location for the car workshop business for Mr. Obembe and if possible propose alternative businesses. 

## 2.1 Sample of  Original dataset

In [1]:
# install libraries
import numpy as np
import pandas as pd
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)
! pip install geopy
from geopy.geocoders import Nominatim
import requests
import json
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
! pip install folium
import folium
print('Libraries installed!')

Libraries installed!


In [2]:
# Download and explore dataset
!wget -q -O 'hamilton_data.json' https://opendata.arcgis.com/datasets/ac6fc684043341f6b1d6298c146a0bcf_1.geojson


with open ('hamilton_data.json') as json_data :
      hamilton_data = json.load(json_data)
hamilton_dataset = hamilton_data['features'][0:10000]

hamilton_dataset

[{'type': 'Feature',
  'properties': {'OBJECTID': 1001,
   'LONGITUDE': '-79.98688084600423',
   'LATITUDE': '43.26070877732673',
   'NUMBER_COMPLETE': '4',
   'UNIT_NUMBER_COMPLETE': None,
   'FULL_STREET_NAME': 'Thornton Trail',
   'SETTLEMENT': None,
   'COMMUNITY': 'Dundas',
   'MUNICIPALITY': 'City of Hamilton',
   'COUNTRY': 'Canada',
   'PROVINCE': 'Ontario'},
  'geometry': {'type': 'Point',
   'coordinates': [-79.986884387345, 43.2607172651189]}},
 {'type': 'Feature',
  'properties': {'OBJECTID': 1002,
   'LONGITUDE': '-79.70825610204196',
   'LATITUDE': '43.23553949279581',
   'NUMBER_COMPLETE': '515',
   'UNIT_NUMBER_COMPLETE': '27',
   'FULL_STREET_NAME': 'North Service Road',
   'SETTLEMENT': None,
   'COMMUNITY': 'Stoney Creek',
   'MUNICIPALITY': 'City of Hamilton',
   'COUNTRY': 'Canada',
   'PROVINCE': 'Ontario'},
  'geometry': {'type': 'Point',
   'coordinates': [-79.70825955290819, 43.23554798910615]}},
 {'type': 'Feature',
  'properties': {'OBJECTID': 1003,
   'LONGI

In [3]:
# display lenth of dictionary hamilton_dataset
print('The length of the Hamilton dataset/dictionary is', len(hamilton_dataset))

The length of the Hamilton dataset/dictionary is 10000


In [4]:
# Create dataframe
column_names  =['ID','Address', 'Longitude', 'Latitude', 'Settlement', 'Community', 'Municipal']
neighborhoods = pd.DataFrame(columns= column_names)

for data in hamilton_dataset:
    neigh_ID = data['properties']['OBJECTID']
    neigh_latlon = data['geometry']['coordinates']
    neigh_lon = neigh_latlon[0]
    neigh_lat = neigh_latlon[1]
    neigh_add = data['properties']['FULL_STREET_NAME']
    neigh_comm = data['properties']['COMMUNITY']
    
    neighborhoods = neighborhoods. append({'ID': neigh_ID, 'Longitude': neigh_lon, 'Latitude': neigh_lat, 
                                           'Address' :  neigh_add, 'Community':neigh_comm}, ignore_index = True)
    
neighborhoods.head()

ID             Address  Longitude   Latitude  Settlement     Community  \
0  1001      Thornton Trail -79.986884  43.260717         NaN        Dundas   
1  1002  North Service Road -79.708260  43.235548         NaN  Stoney Creek   
2  1003      Frances Avenue -79.723719  43.240725         NaN  Stoney Creek   
3  1004     Eastview Avenue -79.754216  43.233877         NaN      Hamilton   
4  1005   Concession 2 West -80.047481  43.264434         NaN   Flamborough   

   Municipal  
0        NaN  
1        NaN  
2        NaN  
3        NaN  
4        NaN

# 2.2 Sample of dataset for Analysis

In [5]:
# Quality check: Examine and clean dataframe
neighborhoods.dropna(axis=1, how='any', thresh=None, inplace=True)
print('The dataframe has {} communities in the city of Hamilton.'. format(len(neighborhoods['Community'].unique())))
print(neighborhoods.shape)
neighborhoods.head()

The dataframe has 6 communities in the city of Hamilton.
(10000, 5)


ID             Address  Longitude   Latitude     Community
0  1001      Thornton Trail -79.986884  43.260717        Dundas
1  1002  North Service Road -79.708260  43.235548  Stoney Creek
2  1003      Frances Avenue -79.723719  43.240725  Stoney Creek
3  1004     Eastview Avenue -79.754216  43.233877      Hamilton
4  1005   Concession 2 West -80.047481  43.264434   Flamborough

In [8]:
 # pandas drop columns with drop function and display unique communities

df = neighborhoods.groupby(['Address', 'Community'], as_index= False).first()

print('The dataframe has {} communities in the city of Hamilton.'. format(len(df['Community'].unique())))
print(df.shape)

The dataframe has 6 communities in the city of Hamilton.
(2455, 5)


In [9]:
# More information on dataframe
print(df['Community'].unique())
df.head()

['Ancaster' 'Hamilton' 'Glanbrook' 'Stoney Creek' 'Flamborough' 'Dundas']


Address  Community    ID  Longitude   Latitude
0       Abbey Close   Ancaster  4594 -80.001446  43.211121
1   Abbington Drive   Hamilton  2991 -79.905134  43.228994
2  Abbotsford Trail  Glanbrook  1825 -79.912267  43.197734
3   Aberdeen Avenue   Hamilton  1675 -79.888418  43.250281
4  Aberfoyle Avenue   Hamilton  1990 -79.809026  43.221419

In [10]:
# Use geop library to get the latitude and longitude values of the city of Hamilton
address    = 'Hamilton, ON'
geolocator = Nominatim(user_agent ='hamilton_explorer')
location   = geolocator.geocode(address)
latitude   = location.latitude
longitude  = location.longitude

print ('The geographical coordinate of the city of Hamilton are {}, {}.'. format(latitude,longitude))

The geographical coordinate of the city of Hamilton are 43.255205, -79.868202.


In [13]:
# Create a map of the city of Hamilton with the communities superimposed 
map_hamilton = folium.Map(location = [latitude,longitude], zoom_start = 10)

# add makers to map
for lat, lng, label in zip(df['Latitude'][0:1000], df['Longitude'][0:1000], df['Address'][0:1000]):
    label = folium.Popup(label, parse_html = True)
    folium.CircleMarker([lat,lng], radius = 5, popup = label, color = 'green', fill = True, fill_color = '#3186cc',
                         fill_opacity = 0.7, parse_html = False). add_to(map_hamilton)

map_hamilton

In [14]:
# Let's explore the first neighborhood in the df dataframe
lati  = df.loc[0,'Latitude']
longi = df.loc[0,'Longitude']
addy  = df.loc[0,'Address']
 
print('Latitude and Longitude values of {} are {}, {}'. format(addy, lati, longi))

Latitude and Longitude values of Abbey Close are 43.211121375501264, -80.001446453813


In [21]:
# The code was removed by Watson Studio for sharing.

Yor credentials:
CLIENT ID :CXH35QZUAPYVZ4IC2BEDC4F4KP2U1TRNVMCAPCGIHCNVNQOR
CLIENT_SECRET:RN4IMJLOJ5UF0JXWALLCLHN3MAXHG01NJBUZC5XKYNL5IHOG
Auto ------ OK!


In [23]:
# function to confirm/extract the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
    if len(categories_list)== 0:
        return None
    else:
        return categories_list[0]['name']

In [24]:
# We are going to explore all the addresses in the dataframe
# The function below repeats the above process to all addresses in the dataframe

def getNearbyVenues(names,latitudes,longitudes, radius = 500):
    venues_list =[]
    for name,lat,lng in zip(names,latitudes,longitudes):
        print(name)
        # create API request url
        url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&v={}&ll={},{}&query={}&radius={}&limit={}'. format(CLIENT_ID, CLIENT_SECRET, VERSION,lat,lng,search_query,
                                                                                                                                    radius,LIMIT)
        results = requests.get(url).json()['response']['venues']
        
        venues_list.append([(name,lat,lng,
                         v['name'], v['location']['lat'], 
                         v['location']['lng'],v['categories']) for v in results])
                      
                    
    nearby_venues = pd.DataFrame( [item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Address', 'Address Latitude', 'Address Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Category']
    return (nearby_venues)


In [25]:
# Apply above function on each address and create new datframe called hamilton_Venues

hamilton_Venues = getNearbyVenues(names = df['Address'], latitudes = df['Latitude'], longitudes= df['Longitude'])

hamilton_Venues

Abbey Close
Abbington Drive
Abbotsford Trail
Aberdeen Avenue
Aberfoyle Avenue
Acacia Street
Academy Street
Acadia Drive
Ackland Street
Acredale Drive
Adair Avenue North
Adair Avenue South
Adele Court
Adeline Avenue
Adis Avenue
Adriatic Boulevard
Afton Avenue
Agnes Street
Aikman Avenue
Airdrie Avenue
Airport Road East
Alanson Street
Albany Avenue
Albert Street
Alberton Road
Albion Falls Boulevard
Albright Road
Alconbury Drive
Alden Street
Alder Court
Aldercrest Avenue
Alderlea Avenue
Aldgate Avenue
Aldridge Court
Alessio Drive
Alexander Road
Alfrin Court
Algonquin Avenue
Alice Street
Allan Avenue
Allan Avenue
Allanbrook Street
Allandale Street
Allenby Avenue
Alma Lane
Alma Street
Alpine Avenue
Alterra Boulevard
Amberly Boulevard
Amelia Street
Amherst Circle
Amore Boulevard
Anchor Road
Anderson Court
Andrew Court
Angus Road
Ann Street
Anna Capri Drive
Annalee Drive
Anson Drive
Anthony Court
Antoinette Court
Appalachian Trail
Appaloosa Trail
Appleblossom Drive
Appleby Road
Appleridge Cour

Address  Address Latitude  Address Longitude  \
0              Aberdeen Avenue         43.250281         -79.888418   
1              Aberdeen Avenue         43.250281         -79.888418   
2              Aberdeen Avenue         43.250281         -79.888418   
3               Academy Street         43.228072         -79.974561   
4               Ackland Street         43.200957         -79.793210   
5           Adair Avenue South         43.233583         -79.791425   
6           Adair Avenue South         43.233583         -79.791425   
7           Adair Avenue South         43.233583         -79.791425   
8               Adeline Avenue         43.241832         -79.791572   
9           Adriatic Boulevard         43.210973         -79.709400   
10                Agnes Street         43.249292         -79.813349   
11                Agnes Street         43.249292         -79.813349   
12               Aikman Avenue         43.250097         -79.846328   
13               Aikman Avenue         43.250097         -79.846328   
14              Airdrie Avenue         43.241079         -79.782540   
15              Airdrie Avenue         43.241079         -79.782540   
16              Airdrie Avenue         43.241079         -79.782540   
17              Alanson Street         43.246454         -79.854145   
18              Alanson Street         43.246454         -79.854145   
19               Albany Avenue         43.247525         -79.806319   
20               Albany Avenue         43.247525         -79.806319   
21               Albany Avenue         43.247525         -79.806319   
22               Albany Avenue         43.247525         -79.806319   
23      Albion Falls Boulevard         43.203320         -79.820254   
24           Aldercrest Avenue         43.191739         -79.894458   
25                Alice Street         43.246859         -79.808332   
26                Alice Street         43.246859         -79.808332   
27                Alice Street         43.246859         -79.808332   
28                Alice Street         43.246859         -79.808332   
29                Allan Avenue         43.260725         -79.943197   
30                Allan Avenue         43.260725         -79.943197   
31                Allan Avenue         43.260725         -79.943197   
32                Allan Avenue         43.245488         -79.803505   
33                Allan Avenue         43.245488         -79.803505   
34                Allan Avenue         43.245488         -79.803505   
35                Allan Avenue         43.245488         -79.803505   
36                Allan Avenue         43.245488         -79.803505   
37            Allandale Street         43.246857         -79.808647   
38            Allandale Street         43.246857         -79.808647   
39            Allandale Street         43.246857         -79.808647   
40            Allandale Street         43.246857         -79.808647   
41              Allenby Avenue         43.232543         -79.879303   
42                 Alma Street         43.270324         -79.954139   
43               Alpine Avenue         43.243287         -79.857302   
44               Alpine Avenue         43.243287         -79.857302   
45                 Anchor Road         43.193347         -79.824416   
46                 Anchor Road         43.193347         -79.824416   
47                  Ann Street         43.262749         -79.972221   
48                  Ann Street         43.262749         -79.972221   
49          Aquasanta Crescent         43.207159         -79.886311   
50                 Arbour Road         43.195645         -79.823455   
51                 Arbour Road         43.195645         -79.823455   
52            Archibald Street         43.246349         -79.805695   
53            Archibald Street         43.246349         -79.805695   
54            Archibald Street         43.246349         -79.805695   
55            Archibald Street         43.24634

In [26]:
# function to confirm/extract the category of the venue
def get_category_type(row):
    try:
        categories_list = row['Category']
    except:
        categories_list = row['venue.Category']
    if len(categories_list)== 0:
        return None
    else:
        return categories_list[0]['name']

In [27]:
# Let us filter the datframe and examine the shape of the new dataframe created
hamilton_Venues['Category']= hamilton_Venues.apply(get_category_type, axis = 1)
print(hamilton_Venues.shape)

(2112, 7)


In [28]:
# Let us inspect the final dataframe
hamilton_Venues


Address  Address Latitude  Address Longitude  \
0              Aberdeen Avenue         43.250281         -79.888418   
1              Aberdeen Avenue         43.250281         -79.888418   
2              Aberdeen Avenue         43.250281         -79.888418   
3               Academy Street         43.228072         -79.974561   
4               Ackland Street         43.200957         -79.793210   
5           Adair Avenue South         43.233583         -79.791425   
6           Adair Avenue South         43.233583         -79.791425   
7           Adair Avenue South         43.233583         -79.791425   
8               Adeline Avenue         43.241832         -79.791572   
9           Adriatic Boulevard         43.210973         -79.709400   
10                Agnes Street         43.249292         -79.813349   
11                Agnes Street         43.249292         -79.813349   
12               Aikman Avenue         43.250097         -79.846328   
13               Aikman Avenue         43.250097         -79.846328   
14              Airdrie Avenue         43.241079         -79.782540   
15              Airdrie Avenue         43.241079         -79.782540   
16              Airdrie Avenue         43.241079         -79.782540   
17              Alanson Street         43.246454         -79.854145   
18              Alanson Street         43.246454         -79.854145   
19               Albany Avenue         43.247525         -79.806319   
20               Albany Avenue         43.247525         -79.806319   
21               Albany Avenue         43.247525         -79.806319   
22               Albany Avenue         43.247525         -79.806319   
23      Albion Falls Boulevard         43.203320         -79.820254   
24           Aldercrest Avenue         43.191739         -79.894458   
25                Alice Street         43.246859         -79.808332   
26                Alice Street         43.246859         -79.808332   
27                Alice Street         43.246859         -79.808332   
28                Alice Street         43.246859         -79.808332   
29                Allan Avenue         43.260725         -79.943197   
30                Allan Avenue         43.260725         -79.943197   
31                Allan Avenue         43.260725         -79.943197   
32                Allan Avenue         43.245488         -79.803505   
33                Allan Avenue         43.245488         -79.803505   
34                Allan Avenue         43.245488         -79.803505   
35                Allan Avenue         43.245488         -79.803505   
36                Allan Avenue         43.245488         -79.803505   
37            Allandale Street         43.246857         -79.808647   
38            Allandale Street         43.246857         -79.808647   
39            Allandale Street         43.246857         -79.808647   
40            Allandale Street         43.246857         -79.808647   
41              Allenby Avenue         43.232543         -79.879303   
42                 Alma Street         43.270324         -79.954139   
43               Alpine Avenue         43.243287         -79.857302   
44               Alpine Avenue         43.243287         -79.857302   
45                 Anchor Road         43.193347         -79.824416   
46                 Anchor Road         43.193347         -79.824416   
47                  Ann Street         43.262749         -79.972221   
48                  Ann Street         43.262749         -79.972221   
49          Aquasanta Crescent         43.207159         -79.886311   
50                 Arbour Road         43.195645         -79.823455   
51                 Arbour Road         43.195645         -79.823455   
52            Archibald Street         43.246349         -79.805695   
53            Archibald Street         43.246349         -79.805695   
54            Archibald Street         43.246349         -79.805695   
55            Archibald Street         43.24634

In [29]:
# Let us also check how many venues were returned for each address
hamilton_Venues.groupby('Address').count()

Address Latitude  Address Longitude  Venue  \
Address                                                                
Aberdeen Avenue                          3                  3      3   
Academy Street                           1                  1      1   
Ackland Street                           1                  1      1   
Adair Avenue South                       3                  3      3   
Adeline Avenue                           1                  1      1   
Adriatic Boulevard                       1                  1      1   
Agnes Street                             2                  2      2   
Aikman Avenue                            2                  2      2   
Airdrie Avenue                           3                  3      3   
Alanson Street                           2                  2      2   
Albany Avenue                            4                  4      4   
Albion Falls Boulevard                   1                  1      1   
Aldercrest Avenue                        1                  1      1   
Alice Street                             4                  4      4   
Allan Avenue                             8                  8      8   
Allandale Street                         4                  4      4   
Allenby Avenue                           1                  1      1   
Alma Street                              1                  1      1   
Alpine Avenue                            2                  2      2   
Anchor Road                              2                  2      2   
Ann Street                               2                  2      2   
Aquasanta Crescent                       1                  1      1   
Arbour Road                              2                  2      2   
Archibald Street                         4                  4      4   
Argyle Avenue                            3                  3      3   
Arkell Street                            1                  1      1   
Arkledun Avenue                          1                  1      1   
Armstrong Avenue                         1                  1      1   
Arno Street                              1                  1      1   
Arthur Avenue North                      1                  1      1   
Arthur Avenue South                      2                  2      2   
Arvin Avenue                             5                  5      5   
Ascoli Drive                             1                  1      1   
Ashford Boulevard                        1                  1      1   
Ashley Street                            6                  6      6   
Ashwood Court                            5                  5      5   
Atessa Drive                             1                  1      1   
Aubrey Avenue                            1                  1      1   
Audubon Street South                     1                  1      1   
Augusta Street                           2                  2      2   
Avondale Street                          6                  6      6   
Aylett Street                            2                  2      2   
Aylmer Crescent                          1                  1      1   
Babcock Street                           1                  1      1   
Baillie Street                           2                  2      2   
Baldwin Street                           1                  1      1   
Balmoral Avenue North                    4                  4      4   
Balsam Avenue South                      2                  2      2   
Bankfield Crescent                       1                  1      1   
Barlake Avenue                           6                  6      6   
Barnaby Street                           2                  2      2   
Barnesdale Avenue North                  2                  2      2   
Barnesdale Avenue South                  2                  2      2   
Barnesdale Boulevard                     2                  2     

In [30]:
# Let us also examine the amount of unique venues that can be curated from all the venues returned and display them
print('There are {} unique categories'. format(len(hamilton_Venues['Category'].unique())))
print(hamilton_Venues['Category'].unique())

There are 17 unique categories
['Automotive Shop' 'Auto Garage' 'Auto Dealership' None 'Hardware Store'
 'Locksmith' 'Auditorium' 'Auto Workshop' 'Urgent Care Center'
 'Shoe Repair' 'College Engineering Building' 'Electronics Store'
 'Car Wash' 'Dry Cleaner' 'Design Studio' 'Insurance Office' 'Building']


# Step 3: Analyze each address

In [31]:
# one hot encoding
hamiltonVenues_onehot = pd.get_dummies(hamilton_Venues[['Category']], prefix = " ", prefix_sep = " ")
# add the address column to the above created dataframe
hamiltonVenues_onehot['Address'] = hamilton_Venues['Address']
# Let us move the address column to the first column
fixed_columns = [hamiltonVenues_onehot.columns[-1] ] + list (hamiltonVenues_onehot.columns[:-1] )
hamiltonVenues_onehot = hamiltonVenues_onehot[fixed_columns]

print(hamiltonVenues_onehot.shape)
hamiltonVenues_onehot.head()
                                                                 

(2112, 17)


Address    Auditorium    Auto Dealership    Auto Garage  \
0  Aberdeen Avenue             0                  0              0   
1  Aberdeen Avenue             0                  0              0   
2  Aberdeen Avenue             0                  0              1   
3   Academy Street             0                  0              1   
4   Ackland Street             0                  1              0   

     Auto Workshop    Automotive Shop    Building    Car Wash  \
0                0                  1           0           0   
1                0                  1           0           0   
2                0                  0           0           0   
3                0                  0           0           0   
4                0                  0           0           0   

     College Engineering Building    Design Studio    Dry Cleaner  \
0                               0                0              0   
1                               0                0              0   
2                               0                0              0   
3                               0                0              0   
4                               0                0              0   

     Electronics Store    Hardware Store    Insurance Office    Locksmith  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

     Shoe Repair    Urgent Care Center  
0              0                     0  
1              0                     0  
2              0                     0  
3              0                     0  
4              0                     0

In [32]:
# Let us group rows by address and by taking the mean of the frequency of the occurence of each category
hamiltonVenues_grouped = hamiltonVenues_onehot.groupby('Address').mean(). reset_index()
hamiltonVenues_grouped

Address    Auditorium    Auto Dealership    Auto Garage  \
0             Aberdeen Avenue      0.000000           0.000000       0.333333   
1              Academy Street      0.000000           0.000000       1.000000   
2              Ackland Street      0.000000           1.000000       0.000000   
3          Adair Avenue South      0.000000           0.000000       0.000000   
4              Adeline Avenue      0.000000           0.000000       0.000000   
5          Adriatic Boulevard      0.000000           0.000000       0.000000   
6                Agnes Street      0.000000           0.000000       0.000000   
7               Aikman Avenue      0.000000           0.000000       0.500000   
8              Airdrie Avenue      0.000000           0.000000       0.000000   
9              Alanson Street      0.500000           0.000000       0.000000   
10              Albany Avenue      0.000000           0.000000       0.250000   
11     Albion Falls Boulevard      0.000000           0.000000       0.000000   
12          Aldercrest Avenue      0.000000           0.000000       0.000000   
13               Alice Street      0.000000           0.000000       0.250000   
14               Allan Avenue      0.000000           0.125000       0.250000   
15           Allandale Street      0.000000           0.000000       0.250000   
16             Allenby Avenue      0.000000           0.000000       1.000000   
17                Alma Street      0.000000           0.000000       0.000000   
18              Alpine Avenue      0.500000           0.000000       0.000000   
19                Anchor Road      0.000000           0.000000       0.000000   
20                 Ann Street      0.000000           0.000000       0.000000   
21         Aquasanta Crescent      0.000000           0.000000       0.000000   
22                Arbour Road      0.000000           0.000000       0.000000   
23           Archibald Street      0.000000           0.000000       0.250000   
24              Argyle Avenue      0.000000           0.000000       0.000000   
25              Arkell Street      0.000000           0.000000       0.000000   
26            Arkledun Avenue      0.000000           0.000000       0.000000   
27           Armstrong Avenue      0.000000           0.000000       0.000000   
28                Arno Street      0.000000           0.000000       0.000000   
29        Arthur Avenue North      0.000000           0.000000       1.000000   
30        Arthur Avenue South      0.000000           0.000000       0.500000   
31               Arvin Avenue      0.000000           0.000000       0.000000   
32               Ascoli Drive      0.000000           0.000000       0.000000   
33          Ashford Boulevard      0.000000           0.000000       0.000000   
34              Ashley Street      0.000000           0.000000       0.333333   
35              Ashwood Court      0.000000           0.000000       0.000000   
36               Atessa Drive      0.000000           0.000000       0.000000   
37              Aubrey Avenue      0.000000           0.000000       1.000000   
38       Audubon Street South      0.000000           1.000000       0.000000   
39             Augusta Street      0.000000           0.000000       0.000000   
40            Avondale Street      0.000000           0.000000       0.000000   
41              Aylett Street      0.000000           0.000000       0.000000   
42            Aylmer Crescent      0.000000           1.000000       0.000000   
43             Babcock Street      0.000000           0.000000       0.000000   
44             Baillie Street      0.000000           0.000000       0.000000   
45             Baldwin Street      0.000000           0.000000       1.000000   
46      Balmoral Avenue North      0.000000           0.000000       0.000000   
47        Balsam Avenue South      0.000000           0.000000       0.000000   
48         Bankfield Crescent      0.000000          

In [33]:
# Now we will print each address along with the top 5 most common enues

num_top_venues = 5
for address_info in hamiltonVenues_grouped['Address']:
    print("----"+address_info+"------")
    temp = hamiltonVenues_grouped[hamiltonVenues_grouped['Address'] == address_info].T.reset_index()
    temp.columns =['venue','freq']
    temp = temp.iloc[1:]
    temp['freq']= temp['freq'].astype(float)
    temp = temp.round({'freq':2})
    print(temp.sort_values('freq', ascending= False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Aberdeen Avenue------
               venue  freq
0    Automotive Shop  0.67
1        Auto Garage  0.33
2         Auditorium  0.00
3    Auto Dealership  0.00
4      Auto Workshop  0.00


----Academy Street------
               venue  freq
0        Auto Garage   1.0
1         Auditorium   0.0
2    Auto Dealership   0.0
3      Auto Workshop   0.0
4    Automotive Shop   0.0


----Ackland Street------
               venue  freq
0    Auto Dealership   1.0
1         Auditorium   0.0
2        Auto Garage   0.0
3      Auto Workshop   0.0
4    Automotive Shop   0.0


----Adair Avenue South------
               venue  freq
0    Automotive Shop  0.67
1         Auditorium  0.00
2    Auto Dealership  0.00
3        Auto Garage  0.00
4      Auto Workshop  0.00


----Adeline Avenue------
               venue  freq
0     Hardware Store   1.0
1         Auditorium   0.0
2    Auto Dealership   0.0
3        Auto Garage   0.0
4      Auto Workshop   0.0


----Adriatic Boulevard------
               venue 

In [34]:
# We also will create dataframe for the above results
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending = False)
    
    return  row_categories_sorted.index.values[0:num_top_venues]

In [35]:
num_top_venues = 10
indicators = ['st','nd','rd']
columns = ['Address']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'. format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'. format(ind+1))
        
# Create dataframe

hamilton_venues_sorted = pd.DataFrame(columns=columns)
hamilton_venues_sorted['Address']= hamiltonVenues_grouped['Address']

for ind in np.arange(hamiltonVenues_grouped.shape[0]):
    hamilton_venues_sorted.iloc[ind, 1:] = return_most_common_venues(hamiltonVenues_grouped.iloc[ind,:], num_top_venues)
    
hamilton_venues_sorted.head()

Address 1st Most Common Venue 2nd Most Common Venue  \
0     Aberdeen Avenue       Automotive Shop           Auto Garage   
1      Academy Street           Auto Garage    Urgent Care Center   
2      Ackland Street       Auto Dealership    Urgent Care Center   
3  Adair Avenue South       Automotive Shop    Urgent Care Center   
4      Adeline Avenue        Hardware Store    Urgent Care Center   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    Urgent Care Center           Shoe Repair             Locksmith   
1           Shoe Repair             Locksmith      Insurance Office   
2           Shoe Repair             Locksmith      Insurance Office   
3           Shoe Repair             Locksmith      Insurance Office   
4           Shoe Repair             Locksmith      Insurance Office   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0      Insurance Office        Hardware Store     Electronics Store   
1        Hardware Store     Electronics Store           Dry Cleaner   
2        Hardware Store     Electronics Store           Dry Cleaner   
3        Hardware Store     Electronics Store           Dry Cleaner   
4     Electronics Store           Dry Cleaner         Design Studio   

            9th Most Common Venue          10th Most Common Venue  
0                     Dry Cleaner                   Design Studio  
1                   Design Studio    College Engineering Building  
2                   Design Studio    College Engineering Building  
3                   Design Studio    College Engineering Building  
4    College Engineering Building                        Car Wash

# Cluster Addresses in Hamilton using Kmeans

In [36]:
# Let us perform clustering analysis
kclusters = 5
hamiltonVenues_grouped_clustering = hamiltonVenues_grouped. drop('Address',1)

kmeans = KMeans(n_clusters = kclusters, random_state =0). fit(hamiltonVenues_grouped_clustering)

hamilton_venues_sorted.insert(0,'Cluster Labels', kmeans.labels_)
hamilton_venues_sorted.head()

Cluster Labels             Address 1st Most Common Venue  \
0               3     Aberdeen Avenue       Automotive Shop   
1               0      Academy Street           Auto Garage   
2               2      Ackland Street       Auto Dealership   
3               3  Adair Avenue South       Automotive Shop   
4               4      Adeline Avenue        Hardware Store   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0           Auto Garage    Urgent Care Center           Shoe Repair   
1    Urgent Care Center           Shoe Repair             Locksmith   
2    Urgent Care Center           Shoe Repair             Locksmith   
3    Urgent Care Center           Shoe Repair             Locksmith   
4    Urgent Care Center           Shoe Repair             Locksmith   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0             Locksmith      Insurance Office        Hardware Store   
1      Insurance Office        Hardware Store     Electronics Store   
2      Insurance Office        Hardware Store     Electronics Store   
3      Insurance Office        Hardware Store     Electronics Store   
4      Insurance Office     Electronics Store           Dry Cleaner   

  8th Most Common Venue           9th Most Common Venue  \
0     Electronics Store                     Dry Cleaner   
1           Dry Cleaner                   Design Studio   
2           Dry Cleaner                   Design Studio   
3           Dry Cleaner                   Design Studio   
4         Design Studio    College Engineering Building   

           10th Most Common Venue  
0                   Design Studio  
1    College Engineering Building  
2    College Engineering Building  
3    College Engineering Building  
4                        Car Wash

In [37]:
# I create a new dataframe that includes the cluster as well as the top three venues of each address

hamilton_merged = df
hamilton_merged = hamilton_merged.join(hamilton_venues_sorted.set_index('Address'), on= 'Address')
hamilton_merged.head(5)

Address  Community    ID  Longitude   Latitude  Cluster Labels  \
0       Abbey Close   Ancaster  4594 -80.001446  43.211121             NaN   
1   Abbington Drive   Hamilton  2991 -79.905134  43.228994             NaN   
2  Abbotsford Trail  Glanbrook  1825 -79.912267  43.197734             NaN   
3   Aberdeen Avenue   Hamilton  1675 -79.888418  43.250281             3.0   
4  Aberfoyle Avenue   Hamilton  1990 -79.809026  43.221419             NaN   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                   NaN                   NaN                   NaN   
1                   NaN                   NaN                   NaN   
2                   NaN                   NaN                   NaN   
3       Automotive Shop           Auto Garage    Urgent Care Center   
4                   NaN                   NaN                   NaN   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                   NaN                   NaN                   NaN   
1                   NaN                   NaN                   NaN   
2                   NaN                   NaN                   NaN   
3           Shoe Repair             Locksmith      Insurance Office   
4                   NaN                   NaN                   NaN   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                   NaN                   NaN                   NaN   
1                   NaN                   NaN                   NaN   
2                   NaN                   NaN                   NaN   
3        Hardware Store     Electronics Store           Dry Cleaner   
4                   NaN                   NaN                   NaN   

  10th Most Common Venue  
0                    NaN  
1                    NaN  
2                    NaN  
3          Design Studio  
4                    NaN

In [38]:
#Let us examine combined dataframe
hamilton_merged.dropna(axis=0, how='any', thresh=None, inplace=True)
hamilton_merged.head(5)

Address     Community    ID  Longitude   Latitude  \
3      Aberdeen Avenue      Hamilton  1675 -79.888418  43.250281   
6       Academy Street      Ancaster  8769 -79.974561  43.228072   
8       Ackland Street  Stoney Creek    54 -79.793210  43.200957   
11  Adair Avenue South      Hamilton  3710 -79.791425  43.233583   
13      Adeline Avenue      Hamilton  3080 -79.791572  43.241832   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
3              3.0       Automotive Shop           Auto Garage   
6              0.0           Auto Garage    Urgent Care Center   
8              2.0       Auto Dealership    Urgent Care Center   
11             3.0       Automotive Shop    Urgent Care Center   
13             4.0        Hardware Store    Urgent Care Center   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
3     Urgent Care Center           Shoe Repair             Locksmith   
6            Shoe Repair             Locksmith      Insurance Office   
8            Shoe Repair             Locksmith      Insurance Office   
11           Shoe Repair             Locksmith      Insurance Office   
13           Shoe Repair             Locksmith      Insurance Office   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3       Insurance Office        Hardware Store     Electronics Store   
6         Hardware Store     Electronics Store           Dry Cleaner   
8         Hardware Store     Electronics Store           Dry Cleaner   
11        Hardware Store     Electronics Store           Dry Cleaner   
13     Electronics Store           Dry Cleaner         Design Studio   

             9th Most Common Venue          10th Most Common Venue  
3                      Dry Cleaner                   Design Studio  
6                    Design Studio    College Engineering Building  
8                    Design Studio    College Engineering Building  
11                   Design Studio    College Engineering Building  
13    College Engineering Building                        Car Wash

In [46]:
# Let's visualize the resulting clusters
map_clusters = folium.Map(location = [latitude,longitude], zoom_start = 11)
x = np.arange(kclusters)
ys = [i + x + (i * x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0,1,len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

#add markers
markers_colors = []
for lat, lon,poi, cluster in zip(hamilton_merged['Latitude'][0:500],  hamilton_merged['Longitude'][0:500],hamilton_merged['Address'][0:500], hamilton_merged['Cluster Labels'][0:500] ):
    label = folium.Popup('Cluster'+ str(cluster), parse_html = True)
    folium.CircleMarker([lat,lon], radius = 5, popup=label, color = rainbow[int(cluster)-1] , fill = True, fill_color = rainbow[int(cluster)-1] ,fill_opacity = 0.7).add_to(map_clusters)
    
map_clusters

In [41]:
# Examine Cluster 1
hamilton_merged.loc[hamilton_merged['Cluster Labels'] == 0, hamilton_merged.columns[ [1] + list(range(5, hamilton_merged.shape[1]))]]

Community  Cluster Labels 1st Most Common Venue  \
6         Ancaster             0.0           Auto Garage   
18        Hamilton             0.0             Locksmith   
43        Hamilton             0.0           Auto Garage   
83        Hamilton             0.0           Auto Garage   
84        Hamilton             0.0             Locksmith   
100   Stoney Creek             0.0           Auto Garage   
116         Dundas             0.0           Auto Garage   
122   Stoney Creek             0.0           Auto Garage   
156       Hamilton             0.0           Auto Garage   
161       Hamilton             0.0           Auto Garage   
174       Hamilton             0.0           Auto Garage   
224       Hamilton             0.0           Auto Garage   
271       Hamilton             0.0           Auto Garage   
290       Ancaster             0.0           Auto Garage   
300       Ancaster             0.0           Auto Garage   
303       Ancaster             0.0           Auto Garage   
321       Hamilton             0.0             Locksmith   
322       Hamilton             0.0           Auto Garage   
332       Hamilton             0.0           Auto Garage   
346   Stoney Creek             0.0           Auto Garage   
359    Flamborough             0.0           Auto Garage   
365       Hamilton             0.0           Auto Garage   
369         Dundas             0.0           Auto Garage   
379       Hamilton             0.0           Auto Garage   
402    Flamborough             0.0           Auto Garage   
403       Ancaster             0.0           Auto Garage   
406       Hamilton             0.0           Auto Garage   
408       Ancaster             0.0           Auto Garage   
423       Hamilton             0.0           Auto Garage   
424       Hamilton             0.0           Auto Garage   
434   Stoney Creek             0.0           Auto Garage   
446       Ancaster             0.0           Auto Garage   
447   Stoney Creek             0.0           Auto Garage   
452       Hamilton             0.0           Auto Garage   
453    Flamborough             0.0           Auto Garage   
456       Ancaster             0.0           Auto Garage   
457       Hamilton             0.0           Auto Garage   
510       Hamilton             0.0           Auto Garage   
549   Stoney Creek             0.0           Auto Garage   
560    Flamborough             0.0           Auto Garage   
573    Flamborough             0.0           Auto Garage   
575       Hamilton             0.0           Auto Garage   
595       Hamilton             0.0             Locksmith   
612       Hamilton             0.0           Auto Garage   
614       Hamilton             0.0           Auto Garage   
626       Hamilton             0.0           Auto Garage   
637       Hamilton             0.0           Auto Garage   
640         Dundas             0.0           Auto Garage   
658   Stoney Creek             0.0           Auto Garage   
659       Hamilton             0.0           Auto Garage   
660       Hamilton             0.0           Auto Garage   
690       Hamilton             0.0           Auto Garage   
693       Hamilton             0.0           Auto Garage   
696         Dundas             0.0           Auto Garage   
731         Dundas             0.0           Auto Garage   
732       Hamilton             0.0           Auto Garage   
748       Hamilton             0.0           Auto Garage   
756       Hamilton             0.0           Auto Garage   
761       Hamilton             0.0           Auto Garage   
795   Stoney Creek             0.0           Auto Garage   
858   Stoney Creek             0.0           Auto Garage   
863       Hamilton             0.0           Auto Garage   
909   Stoney Creek             0.0           Auto Garage   
937       Hamilton             0.0           Auto Garage   
996       Hamilton             0.0             Locksmith   
1015      Hamilton             0.0           Auto

In [42]:
# Examine Cluster 2
hamilton_merged.loc[hamilton_merged['Cluster Labels'] == 1, hamilton_merged.columns[ [1] + list(range(5, hamilton_merged.shape[1]))]]

Community  Cluster Labels 1st Most Common Venue  \
17        Hamilton             1.0       Automotive Shop   
30       Glanbrook             1.0       Automotive Shop   
52        Hamilton             1.0       Automotive Shop   
56          Dundas             1.0       Automotive Shop   
69        Hamilton             1.0       Automotive Shop   
70        Hamilton             1.0       Automotive Shop   
79        Hamilton             1.0       Automotive Shop   
80        Hamilton             1.0       Automotive Shop   
82        Hamilton             1.0       Automotive Shop   
86        Hamilton             1.0       Automotive Shop   
88        Hamilton             1.0       Automotive Shop   
92    Stoney Creek             1.0       Automotive Shop   
95        Hamilton             1.0       Automotive Shop   
108       Hamilton             1.0       Automotive Shop   
110       Hamilton             1.0       Automotive Shop   
112    Flamborough             1.0       Automotive Shop   
119       Hamilton             1.0       Automotive Shop   
129       Hamilton             1.0       Automotive Shop   
130       Hamilton             1.0       Automotive Shop   
131       Hamilton             1.0       Automotive Shop   
132       Hamilton             1.0       Automotive Shop   
136   Stoney Creek             1.0       Automotive Shop   
141   Stoney Creek             1.0       Automotive Shop   
146       Hamilton             1.0       Automotive Shop   
151       Hamilton             1.0       Automotive Shop   
152   Stoney Creek             1.0       Automotive Shop   
157       Hamilton             1.0       Automotive Shop   
159       Hamilton             1.0       Automotive Shop   
163       Hamilton             1.0       Automotive Shop   
164       Hamilton             1.0       Automotive Shop   
168       Hamilton             1.0       Automotive Shop   
171   Stoney Creek             1.0       Automotive Shop   
185   Stoney Creek             1.0       Automotive Shop   
188       Hamilton             1.0       Automotive Shop   
190    Flamborough             1.0       Automotive Shop   
191         Dundas             1.0       Automotive Shop   
196       Hamilton             1.0       Automotive Shop   
201       Hamilton             1.0       Automotive Shop   
202       Hamilton             1.0       Automotive Shop   
227       Hamilton             1.0       Automotive Shop   
229   Stoney Creek             1.0       Automotive Shop   
230       Hamilton             1.0       Automotive Shop   
235    Flamborough             1.0       Automotive Shop   
247         Dundas             1.0       Automotive Shop   
248       Hamilton             1.0       Automotive Shop   
264   Stoney Creek             1.0       Automotive Shop   
292       Hamilton             1.0       Automotive Shop   
295         Dundas             1.0       Automotive Shop   
296         Dundas             1.0       Automotive Shop   
299       Hamilton             1.0       Automotive Shop   
306    Flamborough             1.0       Automotive Shop   
308       Hamilton             1.0       Automotive Shop   
313         Dundas             1.0       Automotive Shop   
335       Hamilton             1.0       Automotive Shop   
337       Hamilton             1.0       Automotive Shop   
338       Hamilton             1.0       Automotive Shop   
339       Ancaster             1.0       Automotive Shop   
343       Hamilton             1.0       Automotive Shop   
345       Hamilton             1.0       Automotive Shop   
350       Hamilton             1.0       Automotive Shop   
368   Stoney Creek             1.0       Automotive Shop   
376       Hamilton             1.0       Automotive Shop   
377       Hamilton             1.0       Automotive Shop   
382       Hamilton             1.0       Automotive Shop   
387       Hamilton             1.0       Automotive Shop   
395       Hamilton             1.0       Automoti

In [43]:
# Examine Cluster 3
hamilton_merged.loc[hamilton_merged['Cluster Labels'] == 2, hamilton_merged.columns[ [1] + list(range(5, hamilton_merged.shape[1]))]]

Community  Cluster Labels 1st Most Common Venue  \
8     Stoney Creek             2.0       Auto Dealership   
103   Stoney Creek             2.0       Auto Dealership   
111   Stoney Creek             2.0       Auto Dealership   
186       Hamilton             2.0           Dry Cleaner   
232   Stoney Creek             2.0       Auto Dealership   
282   Stoney Creek             2.0       Auto Dealership   
320   Stoney Creek             2.0       Auto Dealership   
349   Stoney Creek             2.0       Auto Dealership   
352       Hamilton             2.0           Dry Cleaner   
409       Hamilton             2.0       Auto Dealership   
429       Hamilton             2.0       Auto Dealership   
629   Stoney Creek             2.0       Auto Dealership   
647       Hamilton             2.0       Auto Dealership   
705   Stoney Creek             2.0       Auto Dealership   
735       Hamilton             2.0       Auto Dealership   
772       Hamilton             2.0       Auto Dealership   
877       Hamilton             2.0       Auto Dealership   
914       Hamilton             2.0       Auto Dealership   
963       Hamilton             2.0       Auto Dealership   
1003  Stoney Creek             2.0       Auto Dealership   
1115      Hamilton             2.0           Dry Cleaner   
1119   Flamborough             2.0       Auto Dealership   
1120     Glanbrook             2.0       Auto Dealership   
1201  Stoney Creek             2.0       Auto Dealership   
1237      Hamilton             2.0       Auto Dealership   
1499      Hamilton             2.0       Auto Dealership   
1542  Stoney Creek             2.0       Auto Dealership   
1603      Hamilton             2.0       Auto Dealership   
1605      Hamilton             2.0       Auto Dealership   
1694      Hamilton             2.0       Auto Dealership   
1695  Stoney Creek             2.0       Auto Dealership   
1716      Hamilton             2.0       Auto Dealership   
1751      Hamilton             2.0       Auto Dealership   
1991      Hamilton             2.0       Auto Dealership   
2111  Stoney Creek             2.0       Auto Dealership   
2124      Hamilton             2.0       Auto Dealership   
2175      Hamilton             2.0       Auto Dealership   
2195  Stoney Creek             2.0       Auto Dealership   
2211      Hamilton             2.0       Auto Dealership   
2214      Hamilton             2.0       Auto Dealership   
2223      Hamilton             2.0       Auto Dealership   
2297      Hamilton             2.0       Auto Dealership   
2328      Hamilton             2.0       Auto Dealership   
2337      Hamilton             2.0       Auto Dealership   
2377  Stoney Creek             2.0       Auto Dealership   
2389     Glanbrook             2.0       Auto Dealership   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
8       Urgent Care Center           Shoe Repair             Locksmith   
103     Urgent Care Center           Shoe Repair             Locksmith   
111     Urgent Care Center           Shoe Repair             Locksmith   
186        Auto Dealership    Urgent Care Center           Shoe Repair   
232     Urgent Care Center           Shoe Repair             Locksmith   
282     Urgent Care Center           Shoe Repair             Locksmith   
320     Urgent Care Center           Shoe Repair             Locksmith   
349     Urgent Care Center           Shoe Repair             Locksmith   
352        Auto Dealership    Urgent Care Center           Shoe Repair   
409     Urgent Care Center           Shoe Repair             Locksmith   
429     Urgent Care Center           Shoe Repair             Locksmith   
629     Urgent Care Center           Shoe Repair             Locksmith   
647        Automotive Shop    Urgent Care Center           Shoe Repair   
705     Urgent Care Center           Shoe Repair             Locksmith   
735     Urgent Care Center           Shoe Repair             Locksmith   
772 

In [44]:
# Examine Cluster 4
hamilton_merged.loc[hamilton_merged['Cluster Labels'] == 3, hamilton_merged.columns[ [1] + list(range(5, hamilton_merged.shape[1]))]]

Community  Cluster Labels 1st Most Common Venue  \
3         Hamilton             3.0       Automotive Shop   
11        Hamilton             3.0       Automotive Shop   
19        Hamilton             3.0       Automotive Shop   
22        Hamilton             3.0       Automotive Shop   
38        Hamilton             3.0       Automotive Shop   
39          Dundas             3.0       Automotive Shop   
40        Hamilton             3.0       Automotive Shop   
42        Hamilton             3.0       Automotive Shop   
46        Hamilton             3.0       Automotive Shop   
74        Hamilton             3.0       Automotive Shop   
77        Hamilton             3.0       Automotive Shop   
85    Stoney Creek             3.0       Automotive Shop   
91        Hamilton             3.0       Automotive Shop   
104       Hamilton             3.0             Locksmith   
114       Hamilton             3.0             Locksmith   
121       Hamilton             3.0       Automotive Shop   
126       Hamilton             3.0       Automotive Shop   
128       Hamilton             3.0       Automotive Shop   
137       Hamilton             3.0       Automotive Shop   
148       Hamilton             3.0       Automotive Shop   
169       Hamilton             3.0           Dry Cleaner   
173       Hamilton             3.0       Automotive Shop   
175       Hamilton             3.0       Automotive Shop   
179       Hamilton             3.0       Automotive Shop   
180       Hamilton             3.0       Automotive Shop   
181       Hamilton             3.0       Automotive Shop   
195       Hamilton             3.0       Automotive Shop   
199       Hamilton             3.0       Automotive Shop   
204   Stoney Creek             3.0       Automotive Shop   
207    Flamborough             3.0       Automotive Shop   
208       Ancaster             3.0       Automotive Shop   
209         Dundas             3.0       Automotive Shop   
210       Hamilton             3.0       Automotive Shop   
214   Stoney Creek             3.0       Automotive Shop   
215   Stoney Creek             3.0       Automotive Shop   
217       Hamilton             3.0       Automotive Shop   
218       Hamilton             3.0       Automotive Shop   
225       Hamilton             3.0       Automotive Shop   
240       Hamilton             3.0       Automotive Shop   
261       Hamilton             3.0       Automotive Shop   
263   Stoney Creek             3.0           Auto Garage   
281       Hamilton             3.0       Automotive Shop   
285       Hamilton             3.0       Automotive Shop   
286       Hamilton             3.0       Automotive Shop   
287       Hamilton             3.0       Automotive Shop   
288   Stoney Creek             3.0       Automotive Shop   
316       Hamilton             3.0       Automotive Shop   
336         Dundas             3.0       Automotive Shop   
347   Stoney Creek             3.0       Automotive Shop   
348   Stoney Creek             3.0       Automotive Shop   
351       Hamilton             3.0       Automotive Shop   
357   Stoney Creek             3.0       Automotive Shop   
367       Hamilton             3.0       Automotive Shop   
370       Hamilton             3.0       Automotive Shop   
381       Hamilton             3.0             Locksmith   
410       Hamilton             3.0             Locksmith   
411   Stoney Creek             3.0             Locksmith   
417       Hamilton             3.0       Automotive Shop   
418       Hamilton             3.0       Automotive Shop   
422       Hamilton             3.0       Automotive Shop   
425   Stoney Creek             3.0       Automotive Shop   
431       Hamilton             3.0       Automotive Shop   
440       Hamilton             3.0       Automotive Shop   
450       Hamilton             3.0       Automotive Shop   
462       Hamilton             3.0       Automotive Shop   
472       Hamilton             3.0       Automoti

In [45]:
# Examine Cluster 5
hamilton_merged.loc[hamilton_merged['Cluster Labels'] == 4, hamilton_merged.columns[ [1] + list(range(5, hamilton_merged.shape[1]))]]

Community  Cluster Labels           1st Most Common Venue  \
13        Hamilton             4.0                  Hardware Store   
15    Stoney Creek             4.0              Urgent Care Center   
21        Hamilton             4.0                       Locksmith   
25        Hamilton             4.0              Urgent Care Center   
45          Dundas             4.0              Urgent Care Center   
78        Hamilton             4.0    College Engineering Building   
193       Hamilton             4.0              Urgent Care Center   
309         Dundas             4.0                   Auto Workshop   
315       Hamilton             4.0                   Design Studio   
392    Flamborough             4.0              Urgent Care Center   
401         Dundas             4.0                   Auto Workshop   
469         Dundas             4.0                   Auto Workshop   
476       Hamilton             4.0                     Dry Cleaner   
484   Stoney Creek             4.0                   Design Studio   
545         Dundas             4.0              Urgent Care Center   
628   Stoney Creek             4.0                   Design Studio   
754   Stoney Creek             4.0              Urgent Care Center   
763       Hamilton             4.0                     Dry Cleaner   
775       Hamilton             4.0                     Dry Cleaner   
790   Stoney Creek             4.0              Urgent Care Center   
833    Flamborough             4.0              Urgent Care Center   
852         Dundas             4.0                   Auto Workshop   
926       Hamilton             4.0                       Locksmith   
1005      Hamilton             4.0                   Design Studio   
1006  Stoney Creek             4.0                   Design Studio   
1076        Dundas             4.0                 Automotive Shop   
1101  Stoney Creek             4.0              Urgent Care Center   
1150      Hamilton             4.0                     Dry Cleaner   
1226        Dundas             4.0                   Auto Workshop   
1240  Stoney Creek             4.0              Urgent Care Center   
1253        Dundas             4.0                   Auto Workshop   
1278        Dundas             4.0                   Auto Workshop   
1279      Hamilton             4.0                   Auto Workshop   
1280  Stoney Creek             4.0                   Auto Workshop   
1284      Hamilton             4.0              Urgent Care Center   
1300  Stoney Creek             4.0                   Design Studio   
1319      Hamilton             4.0              Urgent Care Center   
1358      Hamilton             4.0              Urgent Care Center   
1406      Hamilton             4.0              Urgent Care Center   
1422        Dundas             4.0              Urgent Care Center   
1424   Flamborough             4.0              Urgent Care Center   
1457      Hamilton             4.0              Urgent Care Center   
1458        Dundas             4.0                   Auto Workshop   
1461      Hamilton             4.0              Urgent Care Center   
1472        Dundas             4.0                   Auto Workshop   
1473        Dundas             4.0                   Auto Workshop   
1496      Hamilton             4.0              Urgent Care Center   
1511      Ancaster             4.0              Urgent Care Center   
1512   Flamborough             4.0              Urgent Care Center   
1515        Dundas             4.0                 Automotive Shop   
1532   Flamborough             4.0              Urgent Care Center   
1533   Flamborough             4.0              Urgent Care Center   
1560  Stoney Creek             4.0              Urgent Care Center   
1564      Hamilton             4.0              Urgent Care Center   
1596        Dundas             4.0                 Automotive Shop   
1620      Hamilton             4.0    College Engineering Building   
1658  Stoney Creek 